# Case Study

This case study shows you how to analyze one million music tweets, using a Jupyter Notebook integrated with the
**GeoSpock DB**. The case study covers:

- Connect a Jupyter notebook to the GeoSpock database
- Run a number of queries on this data including visualizing the tweets based on their location, as well artist popularity

### Setting up and reading credentials
Please update the host (and port if necessary) in line with your deployment, and save your **GeoSpock DB** credentials
as a username and password separated by a space in a `.geospockcredentials.txt` file in your home directory.

## Connecting a Jupyter notebook to GeoSpock DB
This case study connects to the GeoSpock database using the _presto-python-client_ package. If you wish to use a
different Presto client, some other examples are used in the `Connections` notebook.

Run the following cells first, they import the necessary packages and set up the page. You can then run analysis on the
data from the cells containing the example queries.

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
import datetime
import keplergl
import json

from IPython.core.display import display, HTML
display(HTML("<style>.container { width:90% !important; }</style>"))

%matplotlib inline
pd.set_option('display.max_columns',500)

Please update the below with the correct Presto host and port for your GeoSpock deployment.

In [ ]:
from os.path import expanduser

home = expanduser("~")
with open(home + "/.geospockcredentials.txt", "r") as file:
    x = file.readlines()

[username,password] = x[0].split(" ")
host = "<your deploymeny host>"
port = 8446

In [ ]:
import prestodb.dbapi as presto
import prestodb

conn = presto.Connection(
    host=host,
    port=port,
    user=username,
    http_scheme='https',
    auth=prestodb.auth.BasicAuthentication(username, password)
)

The code below sets up a function to run our queries and output information:

In [ ]:
def runquery(conn,cls,querytext):
    sttime = datetime.datetime.now()
    print("Starting query at: "+str(sttime)+".....")
    cur = conn.cursor()
    cur.execute(querytext)
    rows = cur.fetchall()
    cur.close()
    endtime = datetime.datetime.now()
    print("Finished query at: "+str(endtime)+".")
    tdelt=(endtime-sttime).seconds
    print("Query duration: "+str(tdelt)+" seconds.")
    print("Rows returned: "+str(len(rows)))
    return pd.DataFrame(rows,columns=cls)

In [ ]:
def getcolnames(conn,tbl):
    cur=conn.cursor()
    querycolumnnames="SHOW COLUMNS FROM geospock.default."+tbl
    cur.execute(querycolumnnames)
    cols=cur.fetchall()
    colnames = [col[0] for col in cols]
    cur.close()
    return colnames

## Query one: Visualizing the global distribution of tweets

The first query in this case study enables you to visualize where the tweets on a single day were sent from.  The visualization of the query results highlights one tweet in blue and that will be analyzed further in this case study.

In [ ]:
from os.path import expanduser

home = expanduser("~")
with open(home + "/.geospockcredentials.txt", "r") as file:
    x = file.readlines()

[username,password] = x[0].split(" ")
host = "<your deploymeny host>"
port = 8446

In [ ]:
import prestodb.dbapi as presto
import prestodb

conn = presto.Connection(
    host=host,
    port=port,
    user=username,
    http_scheme='https',
    auth=prestodb.auth.BasicAuthentication(username, password)
)

The code below sets up a function to run our queries and output information:

In [ ]:
def runquery(conn,cls,querytext):
    sttime = datetime.datetime.now()
    print("Starting query at: "+str(sttime)+".....")
    cur = conn.cursor()
    cur.execute(querytext)
    rows = cur.fetchall()
    cur.close()
    endtime = datetime.datetime.now()
    print("Finished query at: "+str(endtime)+".")
    tdelt=(endtime-sttime).seconds
    print("Query duration: "+str(tdelt)+" seconds.")
    print("Rows returned: "+str(len(rows)))
    return pd.DataFrame(rows,columns=cls)

In [ ]:
def getcolnames(conn,tbl):
    cur=conn.cursor()
    querycolumnnames="SHOW COLUMNS FROM geospock.default."+tbl
    cur.execute(querycolumnnames)
    cols=cur.fetchall()
    colnames = [col[0] for col in cols]
    cur.close()
    return colnames

## Query one: Visualizing the global distribution of tweets

The first query in this case study enables you to visualize where the tweets on a single day were sent from.  The visualization of the query results highlights one tweet in blue and that will be analyzed further in this case study.

In [ ]:
QUERY_items_on_date="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE event.timestamp BETWEEN TIMESTAMP '2012-11-02 00:00:00' AND TIMESTAMP '2012-11-03 00:00:00'"

eventcols = getcolnames(conn,'tweet')
eventsondate=runquery(conn,eventcols,QUERY_items_on_date).drop_duplicates().sort_values("timestamp").reset_index().drop("index",axis=1)

w3 = keplergl.KeplerGl(height=500)
w3.add_data(data=eventsondate,name="Tweets")
w3.add_data(data=eventsondate.loc[961,:].to_frame().transpose(),name="MainTweet")

config = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "Tweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}, {"id": "zvhfjbb", "type": "point", "config": {"dataId": "MainTweet", "label": "Point", "color": [50, 26, 151], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 72.2, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["tweet_artistid", "timestamp"], "MainTweet": ["tweet_artistid", "timestamp"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 10.0, "longitude": 0.0, "pitch": 0, "zoom": 1, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")
w3.config = config

In [ ]:
QUERY_items_on_date="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE event.timestamp BETWEEN TIMESTAMP '2012-11-02 00:00:00' AND TIMESTAMP '2012-11-03 00:00:00'"

eventcols = getcolnames(conn,'tweet')
eventsondate=runquery(conn,eventcols,QUERY_items_on_date).drop_duplicates().sort_values("timestamp").reset_index().drop("index",axis=1)

w3 = keplergl.KeplerGl(height=500)
w3.add_data(data=eventsondate,name="Tweets")
w3.add_data(data=eventsondate.loc[961,:].to_frame().transpose(),name="MainTweet")

config = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "Tweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}, {"id": "zvhfjbb", "type": "point", "config": {"dataId": "MainTweet", "label": "Point", "color": [50, 26, 151], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 72.2, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["tweet_artistid", "timestamp"], "MainTweet": ["tweet_artistid", "timestamp"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 10.0, "longitude": 0.0, "pitch": 0, "zoom": 1, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")
w3.config = config

In [ ]:
w3

A screenshot of the generated map can be seen here:
![Whole world](resources/whole_world.png)

## Query two: Distribution of tweets across Paris

Focusing on the city of Paris, this query shows the distribution of all tweets across the city.

In [ ]:
QUERY_items_in_paris="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE st_within(st_point(event.longitude, event.latitude), st_geometryfromtext('POLYGON ((2.225 48.854, 2.250 48.881, 2.320 48.901, 2.396 48.900, 2.410 48.881, 2.412 48.8333, 2.356 48.815, 2.225 48.854))'))"

eventsinparis=runquery(conn,eventcols,QUERY_items_in_paris).drop_duplicates().sort_values("timestamp").reset_index().drop("index",axis=1)

w4 = keplergl.KeplerGl(height=500)
w4.add_data(data=eventsinparis,name="Tweets")
w4.add_data(data=eventsondate.loc[961,:].to_frame().transpose(),name="MainTweet")

config4 = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "Tweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}, {"id": "zvhfjbb", "type": "point", "config": {"dataId": "MainTweet", "label": "Point", "color": [50, 26, 151], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 72.2, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["tweet_artistid", "timestamp"], "MainTweet": ["tweet_artistid", "timestamp"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 48.86, "longitude": 2.32, "pitch": 0, "zoom": 11, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")
w4.config = config4

In [ ]:
w4

A screenshot of the generated map can be seen here:
![Paris](resources/paris.png)

## Query three: Comparison of selected artist against other artists in Paris

This query compares the popularity of the artist mentioned in the selected tweet against the artists mentioned in other tweets in Paris

In [ ]:
QUERY_paris_popular_artists="SELECT id, count(*) as Count \
    FROM geospock.default.tweet AS event \
    WHERE st_within(st_point(event.longitude, event.latitude), st_geometryfromtext('POLYGON ((2.225 48.854, 2.250 48.881, 2.320 48.901, 2.396 48.900, 2.410 48.881, 2.412 48.8333, 2.356 48.815, 2.225 48.854))')) \
    GROUP BY 1 \
    ORDER BY 2 DESC \
    LIMIT 10"

parispopularartists=runquery(conn,["artistid", "Count"],QUERY_paris_popular_artists)

fig, axes = plt.subplots(nrows=1, ncols=1)
plt.rcParams["figure.figsize"] = [16,8.8]
fig.suptitle('Artists by popularity in Paris', fontsize=24)
plt.tight_layout(pad=5, w_pad=5, h_pad=8,rect=[0, 0, 1, 0.98])
parispopularartists.plot.bar("artistid","Count",ax=axes,legend=False,color=['blue','red','red','red','red','red','red','red','red','red'])
axes.set_ylabel("Count")
axes.set_xlabel("Artist ID")
axes.grid(linestyle='-', linewidth='0.5')
plt.show()
plt.close()

In [ ]:
QUERY_paris_our_artist="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE artistid = '356772' \
    AND st_within(st_point(event.longitude, event.latitude), st_geometryfromtext('POLYGON ((2.225 48.854, 2.250 48.881, 2.320 48.901, 2.396 48.900, 2.410 48.881, 2.412 48.8333, 2.356 48.815, 2.225 48.854))'))"

QUERY_paris_not_our_artist="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE artistid != '356772' \
    AND st_within(st_point(event.longitude, event.latitude), st_geometryfromtext('POLYGON ((2.225 48.854, 2.250 48.881, 2.320 48.901, 2.396 48.900, 2.410 48.881, 2.412 48.8333, 2.356 48.815, 2.225 48.854))'))"

paris_our_artist=runquery(conn,eventcols,QUERY_paris_our_artist)
paris_not_our_artist=runquery(conn,eventcols,QUERY_paris_not_our_artist)

w4a = keplergl.KeplerGl(height=500)
w4a.add_data(data=paris_our_artist,name="OurArtistTweets")
w4a.add_data(data=paris_not_our_artist,name="NotOurArtistTweets")

config4a = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "NotOurArtistTweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}, {"id": "zvhfjbb", "type": "point", "config": {"dataId": "OurArtistTweets", "label": "Point", "color": [150, 226, 251], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["tweet_artistid", "timestamp"], "MainTweet": ["tweet_artistid", "timestamp"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 48.86, "longitude": 2.32, "pitch": 0, "zoom": 11, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")
w4a.config = config4a

In [ ]:
w4a

A screenshot of the generated map can be seen here:
![Paris artist](resources/paris_artist.png)

## Query four: Popularity of the artist in Paris and globally

This query determines if the selected artist is popular across the globe as well as in Paris

In [ ]:
QUERY_artist="SELECT event.*\
    FROM geospock.default.tweet AS event \
    WHERE artistid = '356772' \
    AND event.timestamp BETWEEN TIMESTAMP '2012-11-01 00:00:00' AND TIMESTAMP '2012-12-01 00:00:00'"

eventsbyartist=runquery(conn,eventcols,QUERY_artist).drop_duplicates().sort_values("timestamp").reset_index().drop("index",axis=1)

w5 = keplergl.KeplerGl(height=500)
w5.add_data(data=eventsbyartist,name="Tweets")
w5.add_data(data=eventsondate.loc[961,:].to_frame().transpose(),name="MainTweet")
w5.config = config

In [ ]:
w5

A screenshot of the generated map can be seen here:
![Whole world artist](resources/artist_world.png)

It looks like there are more tweets for this artist in Europe, but it is not clear. To see this more clearly, we can break the world up into boxes and look at the number of tweets in each box.

In [ ]:
QUERY_boxed = "WITH events_boxed AS ( \
    SELECT \
        ROUND((latitude + 10.0)/20.0,0) * 20.0 - 10.0 as latitude_box,  \
        ROUND((longitude + 10.0)/20.0,0) * 20.0 - 10.0 as longitude_box \
    FROM geospock.default.tweet AS event \
    WHERE artistid = '356772' \
    AND event.timestamp BETWEEN TIMESTAMP '2012-11-01 00:00:00' AND TIMESTAMP '2012-12-01 00:00:00') \
    SELECT latitude_box, longitude_box, count(*) as num_events \
    FROM events_boxed \
    GROUP BY latitude_box, longitude_box"

eventsbyartistboxed=runquery(conn,["latitude_box", "longitude_box", "num_events"],QUERY_boxed)

w5a = keplergl.KeplerGl(height=500)
w5a.add_data(data=eventsbyartistboxed,name="Tweets")

config5a = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "Tweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude_box", "lng": "longitude_box", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 150], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": {"name": "num_events", "type": "integer"}, "sizeScale": "sqrt"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["num_events"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 10, "longitude": 0, "pitch": 0, "zoom": 1, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")

w5a.config = config5a

In [ ]:
w5a

A screenshot of the generated map can be seen here:
![Artist boxed](resources/artist_world_boxed.png)

## Query five: Artist popularity during a month

This query determines the popularity of the artist over a sample month, to see if their popularity is consistent.

In [ ]:
QUERY_artist2="SELECT date_diff('day', TIMESTAMP '2012-11-01 00:00:00', event.timestamp) AS Day, COUNT(*) as Count \
    FROM geospock.default.tweet AS event \
    WHERE artistid = '356772' \
    AND event.timestamp BETWEEN TIMESTAMP '2012-11-01 00:00:00' AND TIMESTAMP '2012-12-01 00:00:00' \
    GROUP BY 1 ORDER BY 1"

artistbyday=runquery(conn,["Day","Count"],QUERY_artist2)

import matplotlib.pyplot as plt

fig, axes = plt.subplots(nrows=1, ncols=1)
plt.rcParams["figure.figsize"] = [20,10]
fig.suptitle('Tweets per day', fontsize=24)
plt.tight_layout(pad=5, w_pad=5, h_pad=8, rect=[0, 0, 1, 0.98])
artistbyday.groupby('Day').agg({'Count':'sum'}).plot(ax=axes,legend=False)
axes.set_ylabel("Count/day")
axes.set_xlabel("Days since 2012-11-01")
axes.grid(linestyle="-", linewidth='0.5')
plt.show()
plt.close()

## Query six: identify the pattern of tweets from a selected user

This queries visualizes the location of the tweets for a selected user.

In [ ]:
QUERY_tweeter="SELECT event.* \
    FROM geospock.default.tweet AS event \
    WHERE userid = '614442242' \
    AND event.latitude BETWEEN 45 AND 55 AND event.longitude BETWEEN -5 AND 10"

eventstweeter=runquery(conn,eventcols,QUERY_tweeter).drop_duplicates().sort_values("timestamp").reset_index().drop("index",axis=1)

w6 = keplergl.KeplerGl(height=500)
w6.add_data(data=eventstweeter,name="Tweets")
w6.add_data(data=eventsondate.loc[961,:].to_frame().transpose(),name="MainTweet")

config6 = json.loads("""{"version": "v1", "config": {"visState": {"filters": [], "layers": [{"id": "z52nunn", "type": "point", "config": {"dataId": "Tweets", "label": "Point", "color": [187, 0, 0], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 10, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}, {"id": "zvhfjbb", "type": "point", "config": {"dataId": "MainTweet", "label": "Point", "color": [50, 26, 151], "columns": {"lat": "latitude", "lng": "longitude", "altitude": null}, "isVisible": true, "visConfig": {"radius": 72.2, "fixedRadius": false, "opacity": 0.8, "outline": false, "thickness": 2, "strokeColor": null, "colorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "strokeColorRange": {"name": "Global Warming", "type": "sequential", "category": "Uber", "colors": ["#5A1846", "#900C3F", "#C70039", "#E3611C", "#F1920E", "#FFC300"]}, "radiusRange": [0, 50], "filled": true}, "textLabel": [{"field": null, "color": [255, 255, 255], "size": 18, "offset": [0, 0], "anchor": "start", "alignment": "center"}]}, "visualChannels": {"colorField": null, "colorScale": "quantile", "strokeColorField": null, "strokeColorScale": "quantile", "sizeField": null, "sizeScale": "linear"}}], "interactionConfig": {"tooltip": {"fieldsToShow": {"Tweets": ["tweet_artistid", "timestamp"], "MainTweet": ["tweet_artistid", "timestamp"]}, "enabled": true}, "brush": {"size": 0.5, "enabled": false}}, "layerBlending": "normal", "splitMaps": [], "animationConfig": {"currentTime": null, "speed": 1}}, "mapState": {"bearing": 0, "dragRotate": false, "latitude": 48.86, "longitude": 2.32, "pitch": 0, "zoom": 9, "isSplit": false}, "mapStyle": {"styleType": "dark", "topLayerGroups": {}, "visibleLayerGroups": {"label": true, "road": true, "border": false, "building": true, "water": true, "land": true, "3d building": false}, "threeDBuildingColor": [9.665468314072013, 17.18305478057247, 31.1442867897876], "mapStyles": {}}}}""")
w6.config = config6

In [ ]:
w6

A screenshot of the generated map can be seen here:
![Paris tweeter](resources/paris_tweeter.png)

## Adapting the queries and graphs for your own datasets
SQL queries can be submitted using the runquery function, which returns a dataframe.

For matplotlib graphs, the user guide can be found here: https://matplotlib.org

For the kepler maps, there is a user guide here: https://docs.kepler.gl/docs/keplergl-jupyter

To copy and then adapt the maps that are present here, one way is to adjust using the controls on the map itself (e.g. by clicking on the arrow in the top-left and adding/removing layers, colours, point sizes, etc.). You can then save this configuration. For example, to view the configuration for map w6, you can run `w6.config`. To save as a string (which you can then load using `json.loads(...)` as we do above), you could run `json.dumps(w6.config)`. You can also save to a file and read using `json.load(<filename>)`.

Your added graphs then can be set up and displayed using:
```
added_graph = keplergl.KeplerGl(height=500)
added_graph.add_data(data=<results_from_your_query>,name="<DataName>")

config = json.loads("""<your config string>""")
added_graph.config = config

added_graph
```